<a href="https://colab.research.google.com/github/JoshFowlkes/DS-Unit-2-Applied-Modeling/blob/master/module1/assignment_applied_modeling_1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Lambda School Data Science, Unit 2: Predictive Modeling

# Applied Modeling, Module 1

You will use your portfolio project dataset for all assignments this sprint.

## Assignment

Complete these tasks for your project, and document your decisions.

- [ ] Choose your target. Which column in your tabular dataset will you predict?
- [ ] Choose which observations you will use to train, validate, and test your model. And which observations, if any, to exclude.
- [ ] Determine whether your problem is regression or classification.
- [ ] Choose your evaluation metric.
- [ ] Begin with baselines: majority class baseline for classification, or mean baseline for regression, with your metric of choice.
- [ ] Begin to clean and explore your data.
- [ ] Choose which features, if any, to exclude. Would some features "leak" information from the future?

## Reading
- [Attacking discrimination with smarter machine learning](https://research.google.com/bigpicture/attacking-discrimination-in-ml/), by Google Research, with  interactive visualizations. _"A threshold classifier essentially makes a yes/no decision, putting things in one category or another. We look at how these classifiers work, ways they can potentially be unfair, and how you might turn an unfair classifier into a fairer one. As an illustrative example, we focus on loan granting scenarios where a bank may grant or deny a loan based on a single, automatically computed number such as a credit score."_
- [How Shopify Capital Uses Quantile Regression To Help Merchants Succeed](https://engineering.shopify.com/blogs/engineering/how-shopify-uses-machine-learning-to-help-our-merchants-grow-their-business)
- [Maximizing Scarce Maintenance Resources with Data: Applying predictive modeling, precision at k, and clustering to optimize impact](https://towardsdatascience.com/maximizing-scarce-maintenance-resources-with-data-8f3491133050), **by Lambda DS3 student** Michael Brady. His blog post extends the Tanzania Waterpumps scenario, far beyond what's in the lecture notebook.
- [Notebook about how to calculate expected value from a confusion matrix by treating it as a cost-benefit matrix](https://github.com/podopie/DAT18NYC/blob/master/classes/13-expected_value_cost_benefit_analysis.ipynb)
- [Simple guide to confusion matrix terminology](https://www.dataschool.io/simple-guide-to-confusion-matrix-terminology/) by Kevin Markham, with video
- [Visualizing Machine Learning Thresholds to Make Better Business Decisions](https://blog.insightdatascience.com/visualizing-machine-learning-thresholds-to-make-better-business-decisions-4ab07f823415)

In [1]:
# If you're in Colab...
import os, sys
in_colab = 'google.colab' in sys.modules

if in_colab:
    # Install required python packages:
    # category_encoders, version >= 2.0
    # pandas-profiling, version >= 2.0
    # plotly, version >= 4.0
    !pip install --upgrade category_encoders pandas-profiling plotly
    
    # Pull files from Github repo
    os.chdir('/content')
    !git init .
    !git remote add origin https://github.com/LambdaSchool/DS-Unit-2-Regression-Classification.git
    !git pull origin master
    
    # Change into directory for module
    os.chdir('module3')


Requirement already up-to-date: category_encoders in /usr/local/lib/python3.6/dist-packages (2.0.0)
Requirement already up-to-date: pandas-profiling in /usr/local/lib/python3.6/dist-packages (2.3.0)
Requirement already up-to-date: plotly in /usr/local/lib/python3.6/dist-packages (4.1.0)
Reinitialized existing Git repository in /content/.git/
fatal: remote origin already exists.
From https://github.com/LambdaSchool/DS-Unit-2-Regression-Classification
 * branch            master     -> FETCH_HEAD
Already up to date.


# Bringing in the datasets


In [57]:
import pandas as pd 

# Dataset 1, for Cross Fit athelete Data

crossfit_df = pd.read_csv('https://query.data.world/s/rdbhr2ys7lch5xwncuj77b7qnsm26c')
print(crossfit_df.shape)

crossfit_df.head()

(423006, 28)


athlete_id           name  ...     howlong retrieved_datetime
0      2554.0      Pj Ablang  ...   4+ years|                NaN
1      3517.0  Derek Abdella  ...   4+ years|                NaN
2      4691.0            NaN  ...         NaN                NaN
3      5164.0    Abo Brandon  ...   4+ years|                NaN
4      5286.0    Bryce Abbey  ...  1-2 years|                NaN

[5 rows x 28 columns]

In [3]:
from google.colab import files
uploaded = files.upload()

Saving nutrients (1).csv to nutrients (1).csv


In [28]:
# Dataset 2, for macronutrient and micro nutrient breakdown perfood

nutrition_df = pd.read_csv('nutrients (1).csv')
print(nutrition_df.shape)
nutrition_df.head()

(7637, 17)


name  ...     id
0  Beverage, instant breakfast powder, chocolate,...  ...  27481
1  Beverage, instant breakfast powder, chocolate,...  ...  27482
2        Beverage, milkshake mix, dry, not chocolate  ...  27483
3                              Butter oil, anhydrous  ...  27484
4                                     Butter, salted  ...  27485

[5 rows x 17 columns]

# Pandas Profiling Reports

In [0]:
import pandas_profiling
#crossfit_df.profile_report()

In [90]:
nutrition_df.profile_report()

# Some Cleaning & Wrangling(dropping columns, observations etc)

In [0]:
# cleaning up Nutrition DF

# getting rid of the " (g)" in the column names
nutrition_df.columns = nutrition_df.columns.str.rstrip(' (g)')

In [0]:
# cleaning up Crossfit DF
import numpy as np

# getting only observations that have age & weight stats, as these will be most useful in analysis
crossfit_df = crossfit_df[np.isfinite(crossfit_df['age'])]
crossfit_df = crossfit_df[np.isfinite(crossfit_df['weight'])]

# dropping columns that don't appear as though they'll aid in the analysis
crossfit_df = crossfit_df.drop(columns = {'retrieved_datetime', 'athlete_id',
                                          'affiliate'})

In [0]:
mask = ((crossfit_df['weight'] < 400) & (crossfit_df['weight'] > 80))
crossfit_df = crossfit_df[mask]

# using deadlifts less than 1200 since that is the world record deadlift
# using greater than 40 since that would be expected of this class of athlete(and its merely the bar)
mask = ((crossfit_df['deadlift'] < 1200) & (crossfit_df['deadlift'] > 45))
crossfit_df = crossfit_df[mask]

# continuing to get rid of outliers that were obviously entered incorrectly, 
# ie the majority in run5k are in the low thousands, and then theres enties with 8 million lol
mask = crossfit_df['run5k'] < 7000
crossfit_df = crossfit_df[mask]

# setting parameters for height, ie, theres no person thats 2 feet tall and 400 pounds, 
# obviously some sort of entry error 
mask = ((crossfit_df['height'] < 90) & (crossfit_df['height'] > 50))
crossfit_df = crossfit_df[mask]


mask = crossfit_df['pullups'] < 120
crossfit_df = crossfit_df[mask]

In [31]:
nutrition_df.head()

name  ...     id
0  Beverage, instant breakfast powder, chocolate,...  ...  27481
1  Beverage, instant breakfast powder, chocolate,...  ...  27482
2        Beverage, milkshake mix, dry, not chocolate  ...  27483
3                              Butter oil, anhydrous  ...  27484
4                                     Butter, salted  ...  27485

[5 rows x 17 columns]

# Choosing Target(also if it is a regression or classification)

In [0]:
# Target for Nutrtion dataset

# making the food group the target for the nutrtion data set, 
# so based on all the various macro and micro nutrients, can the food group be predicted?
# the bigger picture is to perfectly and accurately predict what an athelete would need
# for optimal performance and with this webapp, they could find the food and it's quantity instantly
# that would best serve their atheletic needs
nutrition_target = 'group'



# Target for Crossfit Dataset


# so the target will be the athlete's weight. 
# this will tie back to nutrition in the final product in that based on all
# the various exercise factors, their stats such as height, gender etc, 
# what will be the optimal nutrtion for that athlete, at that weight, with that given
# activity level 
crossfit_target = 'weight'

# Evaluation Metric & Baseline

In [35]:
# Baseline Majority Class = Vegetables & vegetable product
nutrition_df['group'].value_counts(normalize=True)

Vegetables and Vegetable Products    0.106324
Beef Products                        0.081053
Soups, Sauces, and Gravies           0.065340
Baked Products                       0.064947
Breakfast Cereals                    0.052769
Poultry Products                     0.049889
Fast Foods                           0.047794
Legumes and Legume Products          0.047794
Lamb, Veal, and Game Products        0.045175
Sweets                               0.044651
Pork Products                        0.042949
Fruits and Fruit Juices              0.042949
Baby Foods                           0.042818
Beverages                            0.036402
Finfish and Shellfish Products       0.033390
Dairy and Egg Products               0.031295
Sausages and Luncheon Meats          0.030640
Fats and Oils                        0.028152
Cereal Grains and Pasta              0.023962
Ethnic Foods                         0.021605
Snacks                               0.021213
Nut and Seed Products             

In [36]:
# Baseline Mean Weight
crossfit_df['weight'].mean()

170.8961372830484

# Beginning Data Exploration For Crossfit Dataset


In [65]:
import seaborn as sns
import plotly.express as px
px.scatter(crossfit_df, x='deadlift', y='weight', color='weight')

In [68]:
import seaborn as sns
import plotly.express as px
px.scatter(crossfit_df, x='run5k', y='weight', color='weight')

In [69]:
px.scatter(crossfit_df, x='howlong', y='weight', color='weight')

In [77]:
px.scatter(crossfit_df, x='height', y='weight', color='weight')

In [82]:
px.scatter(crossfit_df, x='pullups', y='weight', color='weight')

# Beginning Data Exploration For Nutrition Dataset

In [84]:
px.scatter(nutrition_df, x='protein', y='group')

In [88]:
px.scatter(nutrition_df, x='calories', y='group', color='calories')

In [89]:
px.scatter(nutrition_df, x='fiber', y='group', color='calories')